# Real-time processing
All of the queries can run in real-time mode. Real-time processing is enabled via callbacks. We illustrate this on the signal generation use case.

# Use case: Signal Generation

We'll compute golden cross signals using 50-second and 200-second moving averages
- 'Entries' is set to 1 when the short-term moving average goes above the long term (i.e., a signal to buy)
- 'Exits' is set to 1 on when the short-term moving average goes below the long term (i.e., a signal to sell)

In [2]:
import onetick.py as otp
data = otp.DataSource('NYSE_TAQ', tick_type='TRD')
data = data.table(PRICE=float, strict=False)
data = data.agg({'SMA50': otp.agg.average(data['PRICE'])}, bucket_interval=50, running=True, all_fields=True)
data = data.agg({'SMA200': otp.agg.average(data['PRICE'])}, bucket_interval=200, running=True, all_fields=True)
data['Entries'] = (data['SMA50'][-1] < data['SMA200'][-1]) & (data['SMA50'] > data['SMA200'])
data['Exits'] = (data['SMA50'][-1] > data['SMA200'][-1]) & (data['SMA50'] < data['SMA200'])

We define a callback that for every tick (i.e., on every trade) will
- print a '.' if there is no signal
- print out the tick followed by 'BUY' on an entry signal
- print out the tick followed by 'SELL' on an exit signal

In [3]:
class GoldenCrossCallback(otp.CallbackBase):
    def process_tick(self, tick, time):
        if not tick['Entries'] and not tick['Exits']:
            print('.', end='')
            return
        print()
        print()
        print(time, tick)
        if tick['Entries']:
            print('BUY')
        if tick['Exits']:
            print('SELL')
        print()

The query will run continuously with the output printed as the events happen if you set start/end times accordingly (see the commented out line).

In [5]:
cb = GoldenCrossCallback()
otp.run(data, symbols='AAPL',
        callback=cb, running=True,
        # start=otp.dt.now(), end=otp.dt.now() + otp.Day(1),
        start=otp.dt(2023,3,7,10), end=otp.dt(2023,3,7,10,10),
)

........................................

2023-03-07 10:06:26.590292 {'COND': '@ TI', 'CORR': 0, 'DELETED_TIME': datetime.datetime(1970, 1, 1, 0, 0), 'EXCHANGE': 'P', 'OMDSEQ': 0, 'PARTICIPANT_TIME': datetime.datetime(2023, 3, 7, 10, 6, 26, 589948), 'PRICE': 154.18, 'SEQ_NUM': 12313, 'SIZE': 1, 'SOURCE': 'N', 'STOP_STOCK': '', 'TICKER': 'AAPL', 'TICK_STATUS': 0, 'TRADE_ID': '519', 'TRF': ' ', 'TRF_TIME': datetime.datetime(1970, 1, 1, 0, 0), 'TTE': '0', 'SMA50': 154.166666666667, 'SMA200': 154.16423076923076, 'Entries': 1.0, 'Exits': 0.0}
BUY

.

2023-03-07 10:07:28.655677 {'COND': '@ TI', 'CORR': 0, 'DELETED_TIME': datetime.datetime(1970, 1, 1, 0, 0), 'EXCHANGE': 'Q', 'OMDSEQ': 0, 'PARTICIPANT_TIME': datetime.datetime(2023, 3, 7, 10, 7, 28, 655659), 'PRICE': 154.15, 'SEQ_NUM': 12455, 'SIZE': 5, 'SOURCE': 'N', 'STOP_STOCK': '', 'TICKER': 'AAPL', 'TICK_STATUS': 0, 'TRADE_ID': '349', 'TRF': ' ', 'TRF_TIME': datetime.datetime(1970, 1, 1, 0, 0), 'TTE': '0', 'SMA50': 154.1500000000005, 'SMA2